In [116]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from numpy.linalg import inv

In [117]:
# Loading data
data_matrix_train, COP_train, data_matrix_test, COP_test, names = np.load('data_center_data_matrix.npy', allow_pickle=True)

In [118]:
# Constructing matrices for min_w ||A w - b||_2**2

matrix_mean = np.mean(data_matrix_train, axis=0)
M = data_matrix_train - matrix_mean
matrix_std = np.std(M, axis=0)
M = M / matrix_std

A = np.hstack([M, np.ones((M.shape[0],1)), -(M.T * COP_train[:,3]).T])
b = COP_train[:,3]

# Test dataset

M_test = (data_matrix_test - matrix_mean) / matrix_std
A_test = np.hstack([M_test, np.ones((M_test.shape[0],1)), -(M_test.T * COP_test[:,3]).T])
b_test = COP_test[:,3]


## Question 3.1

Since we have that $A w=\tilde{x}(t)^{\top} w_1+w_0-y(t) \times \tilde{x}(t)^{\top} w_2$ and $b=y(t)$, then:

$$
A w = b \Rightarrow \tilde{x}(t)^{\top} w_1+w_0-y(t) \times \tilde{x}(t)^{\top} w_2 = y(t)
$$

Solving for $y(t)$, we get:

$$
y(t) = \tilde{x}(t)^{\top} w_1+w_0-y(t) \times \tilde{x}(t)^{\top} w_2 \Rightarrow y(t) + y(t) \times \tilde{x}(t)^{\top} w_2 = \tilde{x}(t)^{\top} w_1+w_0 
$$
$$
\Rightarrow y(t) [1 + \tilde{x}(t)^{\top} w_2] = \tilde{x}(t)^{\top} w_1+w_0 \Rightarrow y(t) = \frac{\tilde{x}(t)^{\top} w_1+w_0}{\tilde{x}(t)^{\top} w_1+w_0}
$$

Finally, as the vectors $\tilde{x}(t)$, $w_1$ and $w_2$ are column vectors of dimension $\mathbb{R}^{d}$, we have that $\tilde{x}(t)^{\top} w_1 = w_1^{\top} \tilde{x}(t)$  and $\tilde{x}(t)^{\top} w_1 = w_1^{\top} \tilde{x}(t)$. Thus, we get that $y(t)$ is given by:

$$
\mathbf{y(t) = \frac{w_1^{\top} \tilde{x}(t)+w_0}{w_1^{\top} \tilde{x}(t)+w_0}}
$$

## Question 3.2

In [119]:
# Solving numpy.linalg.lstsq
w, residuals, rank, s = np.linalg.lstsq(A, b, rcond=None)
print("Parameters using numpy.linalg.lstsq to solve the least square problem:")
print("w = ", w)

Parameters using numpy.linalg.lstsq to solve the least square problem:
w =  [-0.00927821  0.08309371 -0.03672704 ...  0.01980595 -0.03057174
 -0.01188614]


## Question 3.3

To evaluate the quality of the solution, we can use the mean square error (MSE):

$$
MSE = \frac{1}{n} \sum_{i=1}^{n} (y_i - \hat{y}_i)^2
$$


In [120]:
# Mean squared error using the test dataset

residuals = (A_test @ w - b_test)
MSE1 = np.mean(residuals**2)

print("MSE = ", MSE1)

MSE =  780.8984793523671


## Question 3.4

First we can rewrite the target function $f(w)$ as:

$$
f(w) = \frac{1}{2} \|A w - b\|^2 + \frac{\lambda}{2} \|w\|^2 = \frac{1}{2} (A w - b)^{\top} (A w - b) + \frac{\lambda}{2} w^{\top} w 
$$

Then, taking the gradient of $f(w)$:

$$
\nabla {f(w)} = \frac{1}{2} \cdot 2 \cdot A^{\top} (A w - b) + \frac{\lambda}{2} \cdot 2 \cdot w = A^{\top} (A w - b) + \lambda w
$$

Now, making $\nabla {f(w)} = 0$ and solving for $w$:

$$
\nabla {f(w)} = A^{\top} (A w - b) + \lambda w = 0 
$$
$$
\Rightarrow A^{\top} A w - A^{\top} b + \lambda w = 0 \Rightarrow A^{\top} A w + \lambda w = A^{\top} b \Rightarrow (A^{\top} A + \lambda I) w = A^{\top} b 
$$

$$
\Rightarrow \mathbf{w = (A^{\top} A + \lambda I)^{-1} A^{\top} b}
$$

In [121]:
# Define the regularization parameter
lambda_ = 100

# Add regularization to the least squares solution
w = inv(A.T @ A + lambda_ * np.eye(A.shape[1])) @ A.T @ b

print("Parameters:")
print("w = ", w)

Parameters:
w =  [-0.01238313  0.05780406 -0.00127775 ...  0.01590558 -0.03567897
  0.0131232 ]


In [122]:
residuals = (A_test @ w - b_test)
MSE2 = np.mean(residuals**2)

# Create a dictionary with the MSE values
mse_data = {'MSE': [MSE1, MSE2]}

# Create a DataFrame from the dictionary
mse_df = pd.DataFrame(mse_data, index=['Without regularization', 'With l2-regularization'])

# Display the DataFrame
mse_df


MSE
Without regularization  780.898479
With l2-regularization  301.054828

As can be seen above, the Mean Squared Error (MSE) with L2 regularization was lower because L2 regularization helps to prevent overfitting. It does this by adding a penalty term to the loss function, which encourages the model to have smaller weights, leading to a simpler model. This simpler model may not fit the training data perfectly, but it is more likely to generalize better to new, unseen data. Therefore, the lower MSE with L2 regularization indicates that the model is effectively generalizing and not just memorizing the training data.

## Question 3.5

As we have already computed above, the gradient of $f_1(w)$ is:

$$
\nabla f_1 = A^T(Aw - b) + \lambda w
$$

To show that $f_1(w)$ is convex, we need to show that the Hessian matrix $\nabla^2 f_1$ is positive semidefinite. The $\nabla^2 f_1$ is given by:

$$
\nabla^2 f_1 = A^T A + \lambda I
$$

Firstly, it is easy to see that the matrix $\lambda I$ is positive definite since $\lambda > 0$. 

Now, for the matrix $A^T A$, we have to recall that a symmetric matrix A is positive semidefinite if and only if $x^T A x \geq 0$. As $A^T A$ is symmetric and we have that:

$$
x^T A^T A x = (A x)^T A x = ||A x|| \geq 0
$$

we prove that $A^T A$ is positive semidefinite.

Therefore, given that $A^T A + \lambda I$ is also positive semidefinite, $\nabla^2 f_1$ is positive semidefinite, which proves that $f_1$ is a convex function.

## Question 3.6

To calculate the step size $\gamma = \frac{1}{L}$, where $L$ is the Lipschitz value, we need to find an upper-bound of the following expression:

$$
|| \nabla f_1(w2) - \nabla f_1(w_1) || = || A^T (A w_2 - b) + \lambda w_2 - (A^T (A w_1 - b) + \lambda w_1) ||
$$

$$
= || A^T A w_2 - A^T b + \lambda w_2 - A^T A w_1 + A^T b - \lambda w_2 || = || A^T A (w_2 - w_1) + \lambda (w_2 - w_1) ||
$$

$$
= || (A^T A + \lambda I)  (w_2 - w_1) ||
$$

Then, we know that $|| (A^T A + \lambda I)  (w_2 - w_1) || \leq || A^TA + \lambda I ||{op} || w_2 - w_1 ||$, where $|| A^TA + \lambda I ||{op}$ is the operator norm of $A^TA + \lambda I$ given by:

$$
|| A^TA + \lambda I ||_{op} = sup \frac{|| (A^T A + \lambda I)  x ||}{|| x ||} \forall x \in  \mathbb{R}^d
$$

To compute $|| A^TA + \lambda I ||{op}$, we have to take the largest eigenvalue $\lambda{max}$ of the symmetric matrix $A^TA + \lambda I$.

Therefore, $|| \nabla f_1(w2) - \nabla f_1(w_1) || \leq L \cdot || w_2 - w_1 ||$, where:

$$
L = || A^TA + \lambda I ||{op} = \lambda{max}
$$

In [123]:
# Computing the L lipschitz constant
L = np.abs(np.max(np.linalg.eigvals((A.T @ A + lambda_ * np.eye(A.shape[1])))))

print("L = ", L)

L =  3492643.105358818


In [125]:
# Implementing gradient descent

# Define the step size : 1/L


# Lambada paremeter for regularization
lambda_ = 100

alpha = 1/(L+lambda_)
           
# Initialize w0

w0 = np.zeros(A.shape[1])

# Define the number of iterations

n_iter = 1000

# Cost function 
def cost_function(A, b, w, lambda_):
    return np.sum((1/2)*(A @ w - b)**2) + lambda_/2 * np.sum(w**2)

# Gradient
def gradient(A, b, w, lambda_):
    return A.T @ (A @ w - b) + lambda_ * w

# Euclidean norm of the gradient
def norm_gradient(A, b, w, lambda_):
    grad = gradient(A, b, w, lambda_)
    return np.linalg.norm(grad)
    #return np.sqrt(np.sum(gradient(A, b, w, lambda_)**2))

# Gradient descent
w = w0
k=0

condition = True
while (condition):
    k = k + 1
    grad = gradient(A, b, w, lambda_)  
    norm_grad = np.linalg.norm(grad)
    #norm of the gradient
    print("norm_grad = ", norm_grad, "Number of iterations = ", k)
    if norm_grad <= 1:
        condition = False
    w = w - alpha * grad
    

norm_grad =  120927.59130301421 Number of iterations =  1
norm_grad =  34076.2771326001 Number of iterations =  2
norm_grad =  21211.81571965528 Number of iterations =  3
norm_grad =  15571.70203374478 Number of iterations =  4
norm_grad =  13227.15189407459 Number of iterations =  5
norm_grad =  12186.318065810046 Number of iterations =  6
norm_grad =  11632.7682158618 Number of iterations =  7
norm_grad =  11274.008142926035 Number of iterations =  8
norm_grad =  11005.616230536567 Number of iterations =  9
norm_grad =  10786.727924338651 Number of iterations =  10
norm_grad =  10598.937810059539 Number of iterations =  11
norm_grad =  10432.661360012155 Number of iterations =  12
norm_grad =  10282.26685652545 Number of iterations =  13
norm_grad =  10144.134581831582 Number of iterations =  14
norm_grad =  10015.782925098481 Number of iterations =  15
norm_grad =  9895.428709281761 Number of iterations =  16
norm_grad =  9781.744925888614 Number of iterations =  17
norm_grad =  967

### Result: norm_grad =  0.9999709342010202 k =  97547

# 4 Regularization for a sparse model